#### 0 Sales Unit Forecasting
Forecasting model can be build using: <br>
  - *Classical Time series forecasting models* such as ARIMA/SARIMA, ETS and decomposable time series forecasting(Prophet) etc.
  - *Regression-based machine learning models*, where the target is predicted using engineered features. 


In this notebook we will use Regression-based machine learning model forecast the sales.
```original data
Assume:

Daily sales is the target

on_sale is a known exogenous feature (0 = no, 1 = yes)

Date	     Sales	    On_Sale
025-01-01	 120	        0
025-01-02	 135	        1
025-01-03	 128	        0
025-01-04	 142	        1
025-01-05	 150	        1
025-01-06	 147	        0
025-01-07	 155	        1

This table is not yet ready for regression-based forecasting.

Table with features engineered

Feature-engineered table (lags + time components)

We now create:

Lag features: sales_lag_1, sales_lag_2, sales_lag_3

Time features (example): day_of_week

Date	    Sales(Target)	    Sales_Lag_1	    Sales_Lag_2	    Sales_Lag_3	    On_Sale	    Day_of_Week
2025-01-04	142	                128	            135	            120	            1	            Sat
2025-01-05	150	                142	            128	            135	            1	            Sun
2025-01-06	147	                150	            142	            128	            0	            Mon
2025-01-07	155	                147	            150	            142	            1	            Tue

```


##### The Major steps for **Forecasting**:
1. Conduct EDA
2. Prepare a data:
  - Drop the useless columns.
  - Split the data (train and test data)
  - Create a new input features (lag1, lag2.., group mean, rolling means, temporal fearures like Day of the Week, Week of the Year, Months etc.) 
  - Create the target variable/s (based on desired horizon)
  - scale and transform the features if required.
3. Train the model
4. Evaluate the model and perform the diagnostic analysis. 

Note that the steps are general and has to abe adjusted based on forecasting method used. 



 
    
    
    
    
    
    







##### Imports

In [ ]:
# Libraries and frameworks used

import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go


import numpy as np
from numpy import quantile

from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score


import os
import sys
from pathlib import Path

import random


# Add project root to path 
project_root = Path("..").resolve()
sys.path.append(str(project_root/"src"))

import helper_functions as hf
from models import models



# from models import models




##### 1. Get the data
For this project, we will build the model to forecast the product sales demand. <br>

##### **Dataset** 
We will use the tabular dataset from kaggle that contains multiple columns related to sales demand, Inventory and price. The dataset is aggregated on daily basis. <br> <br>
**Dataset Link** <br>
[FMCG Daily Sales Dataset](https://www.kaggle.com/datasets/beatafaron/fmcg-daily-sales-data-to-2022-2024/data)<br>



Downloading data progmatically from kaggle requires authentication, we will mannually download and place the dataset inside this folder.

#### 2. Perform some Exploratory Data Analysis. <br> 
Exploratory Data Analysis helps to transform the data as needed, configure the forecasting job, choosig the right parameters. <br>


##### 2.1 *Examine the basic dataframe structure*

In [4]:
df = pd.read_csv(r"../data/sales_dataset.csv")
df.head()

date     sku     brand    segment category   channel      region  \
0  2022-01-21  MI-006  MiBrand1  Milk-Seg3     Milk    Retail  PL-Central   
1  2022-01-21  MI-006  MiBrand1  Milk-Seg3     Milk    Retail    PL-North   
2  2022-01-21  MI-006  MiBrand1  Milk-Seg3     Milk    Retail    PL-South   
3  2022-01-21  MI-006  MiBrand1  Milk-Seg3     Milk  Discount  PL-Central   
4  2022-01-21  MI-006  MiBrand1  Milk-Seg3     Milk  Discount    PL-North   

   pack_type  price_unit  promotion_flag  delivery_days  stock_available  \
0  Multipack        2.38               0              1              141   
1     Single        1.55               1              3                0   
2     Carton        4.00               0              5              118   
3     Single        5.16               0              2               81   
4     Single        7.66               0              4              148   

   delivered_qty  units_sold  
0            128           9  
1            129           0  
2            161           8  
3            114           7  
4            204          12

In [5]:
print(f"There are {df.shape[0]} rows and {df.shape[1]} columns in the dataset.")

There are 190757 rows and 14 columns in the dataset.


##### 2.2 Data Definition:
1. *sku*: It is a **unique internal code** that a retailer assigns to a specific product variant to track invetory or sales. Each `sku` usually identififes a product by detailes like:
- brand 
- product type
- size
- color 
- model or style
Note that each `sku` can be sold to different `region`, distributed through different `channel`, and packeged in different `pack system`.

2. *brand*: it is a manufacturer's or marketer's identity. Examples: (Gatorage, Faircow)
3. *Segment*:  It is a sub-group within a product category. (Sport Drink, Health Drink)
4. *category*: It is a high level of product grouping. example (Beverage)

```heirarchy
        Category
        └── Segment
                └── Brand
                    └── SKU
```

5. *channel*: It is a sales channel through which the products are delivered to customers.
6. *region*: Is the physical location / geogrphical areas when those products are sold. 
7. *pack_type*: It is how the product is packaged for sale. Same product (sku) is packaged differently and sold in same or diffrent region and channels. 
8. *price_unit*: unit price of that sku sold on a give day, for a specific the channel and in region.
9. *promotion_flag*: It a marker to indicate if the product (sku-pack-type-channel-region) were sold on promotion on that day.
10. *delivery_days*: is a number of days required to deliver a product from the supplying node to the selling node (from manufacturer or manufacturing plant to distrubution or retail outlet), measured as the logistics lead time for a specific `sku x pack_type x channel x region`. This represents supply chain / replenishment lead time, not customer last-mile delivery time.
11. *stock_available*: Quantitity of inventory for specific `sku x pack_type x channel x region` on that day.
12. *delivered_quantity*: Quantity of prpoduct delivered as replenishment for for specific `sku x pack_type x channel x region` on that day.
13. *unit_sold* : Total unit sold for specific `sku x pack_type x channel x region` on that day.



##### 2.3 Check out the data



In [6]:
df_1 = df.copy()

In [7]:
print(f"""
There are {df_1["channel"].nunique()} unique sales channels, {df_1['region'].nunique()} unique regions, {df_1["pack_type"].nunique()} unique pack types sold, for the {df_1['sku'].nunique()} over the period from {df_1['date'].min()} to {df_1['date'].max()}.
Hence, there are {df_1["channel"].nunique() * df_1['region'].nunique() * df_1["pack_type"].nunique() * df_1['sku'].nunique()} time series in the dataset.
      """)


There are 3 unique sales channels, 3 unique regions, 3 unique pack types sold, for the 30 over the period from 2022-01-21 to 2024-12-31.
Hence, there are 810 time series in the dataset.
      


##### 2.3.1 Visualize the individual timeseries to examine the series. 
Since there are 810 series, at `sku x pack_type x channel x region`. There is no way to visualize all the series all together at this level of granularity. So lets quickly examine few of the series by taking  random sku, channel, region and pach_type. 

*Select the random  `sku x pack_type x channel x region` and visualize the series*.


In [8]:
# Select random sku, channel, regioon, pack_type combinations to visualize the missing dates
random_sku = random.choice(list(df_1['sku'].unique()))
random_channel = random.choice(list(df_1['channel'].unique()))
random_region = random.choice(list(df_1['region'].unique()))
random_pack_type = random.choice(list(df_1['pack_type'].unique()))

print(f"Randomly selected combination: SKU={random_sku}, Channel={random_channel}, Region={random_region}, Pack Type={random_pack_type}")


filtered_df = df_1[(df_1['sku'] == random_sku)
                 & (df_1['channel'] == random_channel)
                & (df_1['region'] == random_region)
                & (df_1['pack_type'] == random_pack_type)
               ][['date', 'units_sold']]

fig = px.line(filtered_df,
        x='date',
        y="units_sold",
        markers=True,
        title=f"Units Sold over Time for SKU={random_sku}, Channel={random_channel}, Region={random_region}, Pack Type={random_pack_type}")
fig.show()
# 

Randomly selected combination: SKU=YO-016, Channel=Discount, Region=PL-North, Pack Type=Multipack


From the visual inspection eventhough the series is on daily basis, they dont look continous. Many dates are missing and i believe that these missing dates represents `0 unit sold` that day for that `sku x channel x region x pack_type`. 


*Determine the extent of missing and zero-sales days*
This analysis helps assess whether it is appropriate to build daily forecasting models at the
`SKU × Channel × Region × Pack_Type level.`

If a large proportion of observations (e.g., more than 60% of days) correspond to zero sales, the resulting time series is highly intermittent, making daily sales forecasting at this granularity challenging. In such cases, alternative approaches such as temporal aggregation (e.g., weekly) or higher grain level forecast should be considered.







In [9]:

group_cols=['sku', 'channel', 'region', 'pack_type']
empty_dates = hf.is_date_continous(df_1, date_column='date', group_columns=group_cols)

Found 478582 missing dates in the time series.


In [10]:
print(f"""The raw dataset has {df_1.shape[0]} rows, while the total number of missing dates across all the time series is {empty_dates.shape[0]}.\n
How it is possible? Since first sales date and last sales date differ across the time series, the number of expected dates also differ across the time series.\n
Therefore, the total number of expected dates across all the time series is {df_1.shape[0] + empty_dates.shape[0]} rows.""")

print(f"The first date in the dataset is {df_1['date'].min()}")
print(f"The last date in the dataset is {df_1['date'].max()}")  
print(f"The total number of sales dates in the dataset is {(pd.to_datetime(df_1['date'].max()) - pd.to_datetime(df_1['date'].min())).days + 1} days.")
print(f"The total number of expected rows across all the time series is {((pd.to_datetime(df_1['date'].max()) - pd.to_datetime(df_1['date'].min())).days + 1) * 810}.")



The raw dataset has 190757 rows, while the total number of missing dates across all the time series is 478582.

How it is possible? Since first sales date and last sales date differ across the time series, the number of expected dates also differ across the time series.

Therefore, the total number of expected dates across all the time series is 669339 rows.
The first date in the dataset is 2022-01-21
The last date in the dataset is 2024-12-31
The total number of sales dates in the dataset is 1076 days.
The total number of expected rows across all the time series is 871560.


This indicates that some series did not start sales on 2022-01-21, or that certain SKUs were discontinued in specific region–channel–pack type combinations. In addition, some SKUs were introduced in certain regions at a later date, and some new SKUs or pack types were launched and sold through new channels.

In [11]:
print(f"""Now we understand that that are {empty_dates.shape[0]} instances of missing dates, representing `0 sales.
This makes total of {(empty_dates.shape[0] / (df_1.shape[0] + empty_dates.shape[0])) * 100:.2f}% of missing dates or 0 sales days for the `sku x region x channel x pack_type` combination in the dataset.""")


Now we understand that that are 478582 instances of missing dates, representing `0 sales.
This makes total of 71.50% of missing dates or 0 sales days for the `sku x region x channel x pack_type` combination in the dataset.


As indicated earlier, these missing dates make the time series highly intermittent and sparse, which makes it challenging for forecasting models to learn effectively from the dataset.

We can therefore experiment with one of following two possible solutions:

- Train a model to forecast daily sales at the SKU level only. (I prefer this option)

- Train a model to forecast weekly sales at a lower (or more suitable) level of aggregation.




#### 3 Build a Model to forecaset daily sales at `sku` level

##### 3.1 Prepare a data <br>

*Aggregate the data at sku level*<br>
We will aggregate the data at the SKU level. As a result, we will obtain a more continuous time series, but we will lose information related to region, pack type, and channel. This aggregation also introduces an additional challenge of determining how to aggregate the numerical columns appropriately.

The aggregation strategy for each numerical field is as follows:

- `stock_available`: total sum is appropriate at the SKU level.

- `units_sold`: total sum is appropriate at the SKU level.

- `delivered_qty`: total sum is appropriate at the SKU level.

- `promotion`: average value will be used.

- `delivered_days`: average value is suitable.

- `price`: average value is suitable.









*Validate each unique `sku` belongs to only one combination of `brand x catagory x segment`.*




In [12]:
# Validate if sku blongs to multiple brands, channels, regions combinations

df_2 = df_1.groupby(["sku"]).agg(
    {
        "brand": "nunique",
        "segment": "nunique",
        "category": "nunique"
        
        }
).reset_index()
filtred_df_2 = df_2[
    (df_2['brand'] > 1) |
    (df_2['segment'] > 1) |
    (df_2['category'] > 1)
  ]

print(f"There are {filtred_df_2.shape[0]} skus that belong to multiple brands, segments or categories.")

There are 0 skus that belong to multiple brands, segments or categories.


This confirms that each `sku` belongs to only a single combination of `brand x category x segment`.
For the modeling we do not need brand, category, segment as sku itself os a proxy of the values of these columns, for EDA we utilize these columns

In [13]:
# Aggregate the data

group_cols = ['date', 'sku', 'brand', 'category', 'segment']

df_agg_sku = df_1.groupby(group_cols).agg(
    {
        "stock_available": "sum",
        "units_sold": "sum",
        "delivered_qty": "sum", 
        "promotion_flag": "mean",
        "delivery_days":"mean",
        "price_unit": "mean"
}
).reset_index()



In [14]:
print(F"After the aggregation as sku level, the dataset has {df_agg_sku.shape[0]} rows and {df_agg_sku.shape[1]} columns.")

After the aggregation as sku level, the dataset has 24945 rows and 11 columns.


In [15]:
df_agg_sku .head()

date     sku     brand category    segment  stock_available  \
0  2022-01-21  MI-006  MiBrand1     Milk  Milk-Seg3              985   
1  2022-01-22  MI-006  MiBrand1     Milk  Milk-Seg3             1390   
2  2022-01-22  MI-026  MiBrand4     Milk  Milk-Seg2              666   
3  2022-01-23  MI-006  MiBrand1     Milk  Milk-Seg3             1446   
4  2022-01-23  MI-026  MiBrand4     Milk  Milk-Seg2              965   

   units_sold  delivered_qty  promotion_flag  delivery_days  price_unit  
0          85           1231        0.250000       2.875000     4.82875  
1         119           1379        0.142857       3.428571     5.08000  
2          48            792        0.000000       2.200000     5.38200  
3         122           1463        0.125000       3.750000     5.83625  
4          75            932        0.166667       3.000000     4.68500

In [16]:
# validate if there are still missing dates after aggregation
empty_dates_after_agg = hf.is_date_continous(df_agg_sku, date_column='date', group_columns=['sku'])
print(f'Thre are {empty_dates_after_agg.shape[0]} missing dates found after the data aggrefations.')

No missing dates found in the time series.
Thre are 0 missing dates found after the data aggrefations.


##### 3.2 Exploratory Data Analysis

##### 3.2.1 Visuallize the timeseries

In [17]:
# visualize the time series at sku level 
# We will select the for raandom skus and plot the timeseries as subplots

random_sku = random.choices(list(df_agg_sku['sku'].unique()), k=4)    

# Make a subplot with 2 rows and 2 columns
fig = make_subplots(rows=2, cols=2,
                    subplot_titles=[f"SKU: {sku}" for sku in random_sku]
                   )

for i, sku in enumerate(random_sku):
    filtered_df_sku = df_agg_sku[df_agg_sku['sku'] ==sku][['date', 'units_sold']]
    fig.add_trace(
        go.Scatter(
            x=filtered_df_sku['date'],
            y=filtered_df_sku['units_sold'],
            mode='lines',
         
        ),
        row=(i // 2) + 1,
        col= (i % 2) + 1
    )
fig.update_layout(title_text="Units Sold over Time for Randomly Selected SKUs", height=800, width=1400)
fig.show()


Insights:
The plots show daily units sold over time for four randomly selected SKUs. Several common patterns and insights emerge:

1. Seasonality and Cyclic Behavior<br>
All  SKUs exhibit noticeable cyclical patterns, suggesting the presence of seasonality (likely annual or semi-annual). Peaks and troughs recur over time rather than showing purely random behavior.

2. High Short-Term Volatility<br>
Daily sales for each SKU are highly volatile, with frequent spikes and drops. This indicates noisy demand at a daily level, which can make short-horizon forecasting challenging without smoothing or aggregation.

3. SKU-Specific Demand Levels<br>

    - Some SKUs (e.g., YO-014, YO-009) show consistently higher average sales compared to others.
    
    - The magnitude of variability also differs by SKU, implying heterogeneous demand dynamics across products.
    
4. Non-Stationary Behavior<br>
The mean sales level appears to shift over time for several SKUs (e.g., gradual increases or decreases), suggesting non-stationarity. This reinforces the need for models that can handle trends and seasonality.

5. No Extended Zero-Sales Periods<br>
Unlike sparse region–channel–pack-level series, SKU-level aggregation results in continuous sales with no long zero-demand stretches, making the data more suitable for time-series modeling.inter and sfor some The plots show daily units sold over time for four randomly selected SKUs. Several common patterns and insights emerge:




 








##### 3.2.2 Analyze the distributions of sales units of skus
To enable a meaningful analysis of the distribution of sales units for each SKU, we first compute summary statistics such as median units sold, interquartile range, and upper-fence thresholds. These metrics help improve the interpretability of the visualizations and also provide useful inputs for subsequent feature engineering.

In [18]:
# Calculate the metrices at sku lebvel and merge it back to the aggregated dataframe.

agg_df_metrics = df_agg_sku.groupby("sku").agg({
    "units_sold": ["mean", "median", "std", 
                   lambda x: x.quantile(0.25), lambda x: x.quantile(0.75)]
}).reset_index()


agg_df_metrics.columns = ['sku', 'mean_units_sold', 'median_units_sold', 'std_units_sold', 'q25_units_sold', 'q75_units_sold']

# create a column to calculate the upper fence
agg_df_metrics['upper_fence'] =  agg_df_metrics['q75_units_sold'] + 1.5 * (agg_df_metrics['q75_units_sold'] - agg_df_metrics['q25_units_sold'])
agg_df_metrics.head()
# 

sku  mean_units_sold  median_units_sold  std_units_sold  q25_units_sold  \
0  JU-021       137.402210              131.0       46.214170           104.0   
1  MI-002       144.529501              141.0       43.922395           114.0   
2  MI-006       123.255576              118.0       39.074987            97.0   
3  MI-008       131.568254              124.0       44.312924           100.0   
4  MI-011       132.642633              126.5       45.903669           102.0   

   q75_units_sold  upper_fence  
0          165.00      256.500  
1          172.00      259.000  
2          140.25      205.125  
3          153.00      232.500  
4          152.00      227.000

*Merge the `agg_df_metrics` with the `df_agg_sky` df*



In [19]:
df_agg_sku_metrics_merged = df_agg_sku.merge(agg_df_metrics, on="sku", how="left")

In [20]:
df_agg_sku_metrics_merged.head()

date     sku     brand category    segment  stock_available  \
0  2022-01-21  MI-006  MiBrand1     Milk  Milk-Seg3              985   
1  2022-01-22  MI-006  MiBrand1     Milk  Milk-Seg3             1390   
2  2022-01-22  MI-026  MiBrand4     Milk  Milk-Seg2              666   
3  2022-01-23  MI-006  MiBrand1     Milk  Milk-Seg3             1446   
4  2022-01-23  MI-026  MiBrand4     Milk  Milk-Seg2              965   

   units_sold  delivered_qty  promotion_flag  delivery_days  price_unit  \
0          85           1231        0.250000       2.875000     4.82875   
1         119           1379        0.142857       3.428571     5.08000   
2          48            792        0.000000       2.200000     5.38200   
3         122           1463        0.125000       3.750000     5.83625   
4          75            932        0.166667       3.000000     4.68500   

   mean_units_sold  median_units_sold  std_units_sold  q25_units_sold  \
0       123.255576              118.0       39.074987            97.0   
1       123.255576              118.0       39.074987            97.0   
2       141.696744              138.0       39.695596           115.0   
3       123.255576              118.0       39.074987            97.0   
4       141.696744              138.0       39.695596           115.0   

   q75_units_sold  upper_fence  
0          140.25      205.125  
1          140.25      205.125  
2          165.00      240.000  
3          140.25      205.125  
4          165.00      240.000

In [21]:
fig = px.box(
    data_frame = df_agg_sku_metrics_merged.sort_values(by="median_units_sold", ascending=False),
    x="sku",
    y="units_sold", 
    title="Distribution of Units Sold per SKU"

  
)
fig.update_layout(height=600, width=1400)

fig.show()

Insights from the Distribution of Units Sold by SKU

1. Daily sales range <br>
For most SKUs, daily units sold typically range between ~40 and ~320 units, with occasional spikes exceeding 400 units. These extreme values appear across SKUs and may be driven by promotions, stock clearances, or unusual demand events.

2. Category-level differences in demand<br>
SKUs belonging to the yogurt and snack bar categories show higher medians and wider interquartile ranges compared to SKUs from the milk, juice, and ready-made meal categories. This indicates structurally higher and more volatile demand for these categories.

3. Presence of extreme values (outliers)<br>
There are multiple instances where daily sales exceed the typical range for a given SKU. While some of these may represent genuine demand surges (e.g., promotions), they can also introduce noise and instability in model training if not handled carefully.

4. Within-category similarity vs. across-category variability<br>
A notable pattern is that SKUs within the same category exhibit very similar distribution shapes (median, spread, and tail behavior), whereas clear differences exist across categories. This suggests that category-level effects explain a significant portion of demand variability.

##### 3.2.3 Analyze the relationship between sales unit and other variables
There are features such as unit_price, stock_available, delivery_days, delivery_quy that may have some relationship with the units sold. Lets analyze

In [22]:
cols = ['stock_available', 'delivered_qty', 'promotion_flag', 'delivery_days', 'price_unit']

In [23]:
fig = make_subplots(rows=2, cols=3,
                    subplot_titles=[f"Units sold vs  {col}" for col in cols],
                    shared_yaxes=False)
for i, col, in enumerate(cols):
    fig.add_trace(
        go.Scatter(
            y=df_agg_sku_metrics_merged['units_sold'],
            x=df_agg_sku_metrics_merged[col],
            mode='markers'
        ),
        row=(i // 3) + 1,
        col=(i % 3) + 1
    )

fig.update_layout(title_text="Scatter Plots of Features vs Units Sold", height=600, width=1100, showlegend=False)
fig.show()

Insights:
1. Strong positive relationship between `units sold` and `stock_available`. However the scatter diabgram depicts the triangular shape, increased variance in units sales as stock available increases. This indicate that the stock availability is necessary but not sufficient to drive the sales.

2. Strong positive correlationship between `units sold` and `delivered quantity`. It also depicts the same triangle shape, indicating supply side constraint. Higher delivered quantity increase sales but does not necessarily drive sales. 

3. Promotions are associated with higher average sales, but the effect is highly variable. 

4. Delivery days and unit price does not show any observable pattern. But these can have interaction effect on sales. No linear relationship but pattern can bee seen if we transform the unit sold.



In [24]:
correlation_matrics = df_agg_sku_metrics_merged[[
    col for col in df_agg_sku_metrics_merged.columns if col not in ['date', 'sku', 'brand', 'category', 'segment']
    ]
    ].corr()
correlation_matrics 

heat_map = px.imshow(
    correlation_matrics,
    text_auto=True,
    title="Correlation Matrix of Features"
)

heat_map.update_layout(height=600, width=800)

    


Insights:
1. The Larger yellow block on lower right are the metrices such as mean, median, upper quantial etc. These features are highly corellated to each other so we can only keep mean for the modelling as to avoid multicolleanirity.
2. Stock available and delivered quantity are also highly correlated and both have similar correlation with units sold. So we will just keep. stock_available for the modelling.
3. We can also create new feature `sell through rate` by calculating  `units sold / stock available`. 
4. `promotion flag` has also positive correlatiion with units sold.



The scatter plots above resemble cloud shape. There is almost 0 slope in this data. Threfore the price is not the global predictor of sales. A high price doesn't necessarily mean low sales and vice a versa. 

However, relative price or price index can have influence in the sales. This is because influence 10 percent increase of one sku might not the same as 10 percent increase in another sku. <br>
So we will calculate the price index by sku, category, segment, and brand, see their relationshiop and analyze the relationship with units sold.

*Calcutate the Price Index*

In [25]:
price_index_columns = ['category', 'brand', 'sku', 'segment']

for col in price_index_columns:
    df_agg_sku_metrics_merged[f"price_index_{col}"] = (df_agg_sku_metrics_merged['price_unit'] / 
                                                      df_agg_sku_metrics_merged.groupby(col)['price_unit'].
                                                      transform(lambda x: x.shift(1).expanding().mean())
                                                )

In [26]:
index_columns = [
    'price_index_sku',
    'price_index_category',
    'price_index_segment',
    'price_index_brand'
]

df_correlation = df_agg_sku_metrics_merged[index_columns + ['units_sold']].corr()
px.imshow(
    df_correlation,
    text_auto=True,
    title="Correlation Matrix of Price Indices vs log(Units Sold)"
).update_layout(height=500, width=500).show()

As expected the the price idices are perfectly correlated. So we can keep only one price index for the further analysis.
So we will take `price_index_sku`.

Another, important consideration is that the sales is limmited by the stock contraints. For instance, if there are only 10 units available in a day, then you cannot sell more than a 10 units. Because this is stockout, and hence if there is a stockout you sales on that day doesnot reflect the true demand.

*Calculate the stockout*

In [27]:
df_agg_sku_metrics_merged['stockout_flag'] = np.where(df_agg_sku_metrics_merged['stock_available'] <= df_agg_sku_metrics_merged["units_sold"],
                                                      "yes", "no")


stock_out = df_agg_sku_metrics_merged[df_agg_sku_metrics_merged['stockout_flag'] == "yes"]
print (f"There are {stock_out.shape[0]} rows where stock available is less than or equal to units sold.")

There are 0 rows where stock available is less than or equal to units sold.


In [28]:
fig = px.scatter(
    df_agg_sku_metrics_merged,
    x="price_index_sku",
    y="units_sold",
    color='promotion_flag',

    title="Scatter Plot of Price Index (SKU) vs log(Units Sold) with Trendline"
)
fig.update_layout(height=600, width=800)
fig.show()

Insights:
- There is not any correlation between price_index and units sold. Promotional flag is influentional feature as it can be seen that light color markes are mostly on upper side of the chart. 


*Calculate the relative mean unit sold per sku and analyze* <br>
We have calulated the global average unit sold but we can also calculate the relative mean unit sold per sku and see how it far the daily unit sold is from the relative mean. 
Note that we sould not take the `units_sold` as it is to calculate the metrics except for average, but that also only in the trainig data. We should take the `lagged version of units sold`, so that for the prediction time we know the the yersterday unit sold. 

In [29]:
df_agg_sku_metrics_merged['units_sold_yesterday'] = df_agg_sku_metrics_merged.groupby('sku')['units_sold'].shift(1)
df_agg_sku_metrics_merged['mean_units_sold_relative'] = df_agg_sku_metrics_merged['units_sold_yesterday'] / df_agg_sku_metrics_merged['mean_units_sold']


In [30]:
fig = px.scatter(
    df_agg_sku_metrics_merged,
    y="units_sold",
    x="mean_units_sold_relative",
    color="promotion_flag",
    title="Unit sold vs Mean units sold (relative)"
)
fig.show()



The scatter plot of Unit Sold vs. Mean Units Sold (Relative) validates our feature engineering strategy: a clear upward trend demonstrates that relative historical momentum is a strong indicator of current sales volume. Furthermore, the concentration of promotional activity (yellow/orange) at higher index levels confirms that this feature effectively captures the 'halo effect' of marketing campaigns on SKU demand."

<br>
For the modeling we should create this feature only after spliting the dataset into train and test sets as to prevent data leakage. This is because for example say in december (for which we are predicting) sales are naturally high, this inflates the average in the training data. 

*Caculate the relative weekly and monthly moving averages by sku and analyze* <br>
We will calculate the moving average (weekly and monthly) and understand the seasonality and trend closely.

In [31]:
df_agg_sku_metrics_merged['weekly_ma_units_sold'] = df_agg_sku_metrics_merged.groupby("sku")['units_sold_yesterday']\
    .transform(lambda x: x.rolling(window=7).mean())
df_agg_sku_metrics_merged['monthly_ma_units_sold'] = df_agg_sku_metrics_merged.groupby("sku")['units_sold_yesterday']\
    .transform(lambda x: x.rolling(window=30).mean())

df_agg_sku_metrics_merged['relative_weekly_ma_units_sold'] = df_agg_sku_metrics_merged['units_sold_yesterday'] / df_agg_sku_metrics_merged['weekly_ma_units_sold']
df_agg_sku_metrics_merged['relative_monthly_ma_units_sold'] = df_agg_sku_metrics_merged['units_sold_yesterday'] / df_agg_sku_metrics_merged['monthly_ma_units_sold']

In [32]:
df_relative_metrices = df_agg_sku_metrics_merged[['date','sku', 'units_sold', "weekly_ma_units_sold", "monthly_ma_units_sold", "relative_weekly_ma_units_sold", "relative_monthly_ma_units_sold"]].dropna()

In [33]:
random_skus = random.choices(list(df_relative_metrices['sku'].unique()), k=2)
fig = make_subplots(
    rows=2, 
    cols=1,
    subplot_titles=[f"SKU: {random_sku[0]}", f"SKU: {random_sku[1]}"]
)

for i, sku in enumerate(random_skus):
    filter_df_sku = df_relative_metrices[df_relative_metrices['sku'] == sku][['date', 'relative_weekly_ma_units_sold', 'relative_monthly_ma_units_sold', 'weekly_ma_units_sold', 'monthly_ma_units_sold']]

    line = px.line(
        data_frame=filter_df_sku,
        x=filter_df_sku['date'],
        y=['weekly_ma_units_sold', 'monthly_ma_units_sold'])
    for trace in line.data:
        fig.add_trace(trace, row=i+1, col=1)
fig.layout.update(title_text="Weekly and Monthly MA Units Sold for Randomly Selected SKUs", height=600, width=1000)


fig.show()

The weekly MA has freqent spikes and represent short term demend fluctuations and local trends. It reacts quickly to promotion, seasonal spikes and random consumer behaviour.
<br>
Monthly MA filter out the noise to show the broader health and direction of sku's sales.

We can create following features:
- Momentam signal (wma/mma) : when this ratio > 1 it can indicate the upward trend momentum and vice versa.
- Mean Reversion - A feature that measure the distance between the lines . These helps model to predict when sales spike is likely to end and return to normal. 

Note : To avoid the data leakage, these features need to be lagged. 

*Caculate the sell through rate* <br>
Lets calculate the  yesterday's sell through rate dividing the yesterday's by yesterday's stock available.

In [34]:
df_agg_sku_metrics_merged['sell_through_rate_yesterday'] = df_agg_sku_metrics_merged['units_sold_yesterday'] / df_agg_sku_metrics_merged.groupby('sku')['stock_available'].shift(1)

In [35]:
px.scatter(
    df_agg_sku_metrics_merged,
    x="sell_through_rate_yesterday",
    y="units_sold",
    color='promotion_flag',
    title= "Sell Through Rate Yesterday vs Units Sold"
).show()

There is a clear upward "wedge" shape. As the sell-trough rate from yesterday increases, the likelyhood of high sales today increases significantly. 
This feature tells model not just that sales were high but sales were relative to what was available. ---a demand velocity.
Notice that the low sell through rates (0.05 to 0.1), the units sold are very tightly clustered at the bottom. This allows model to predict "low sales" with hich confidence in those scenarios. 
It also interacts with todays inventory available. Todays inventory is high but yesterdays STR is low then model learns the sales will be, so predicts low sells.

*Visualize the distribution of numerical feature*

In [36]:
numerical_columns = ["delivery_days", "stock_available", "delivered_qty", "sell_through_rate_yesterday"]

fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=[col for col in numerical_columns]

)
for i, col in enumerate(numerical_columns):
    fig.add_trace(
        go.Histogram(
            x=df_agg_sku_metrics_merged[col],
            name=col,
            nbinsx=50
        ),
        row=(i // 2) + 1,
        col=(i % 2) + 1
    )
fig.update_layout(title_text="Distribution of Numerical Features", height=400, width=800, showlegend=False)
fig.show()



In the above histogram subplots, delivery_days and stock_available exhibit distributions that are close to normal. In contrast, delivered_qty and sell-through rate are noticeably skewed. Since delivered_qty is highly positively correlated with stock_available, it will not be used as a separate feature to avoid redundancy. We will initially include the sell-through rate as a feature in its original form; if model performance does not improve, appropriate transformations will be applied.

So far from the EDA we understand that some features such as `promotion_flag`and `stock_available` are high valuable for the forecasting sales unit. Besides, we also found that some engineered features can capture important pattern in the data. Feature like weekly_average_units_sold, monthly_average_units_sold are also useful. price_index, mean_units_sold_relative,  relative_weekly_average_units_sold can help to capture the signals in units sold.<br>

However creating these feature needs careful consideration as it can cause data leakage.
Lets explain what this each feature is and how we prepare these features to avoid data leakage.

1. price_index : we calculate price index by `price of sku on the day/ average price of that sku` . At first glance it looks fine to calulate the average of price from each sku by taking the whole dataset, because we know the price during the time we make prediction. However, we use the future price (price of the sku in the validation or test set) to calculate the average is still a data leakage. For example in the test dataset the price of the sku is 500, but in training is 300, and if we consider both to calculate the average, its average would be 400. Why this is bad?  The model in the training phase (where price is 300) will see a Price Index of $300 / 400 = 0.75$. The model learns a false rule: "When Price Index is 0.75, sales are high." However, in the real world on that same day, the average price known to you was actually 300, making the real Price Index 1.0. By using the future price of 500 to pull the average up to 400, you gave the model a "hint" that prices would eventually rise. During testing, when the price is 500 and the index becomes 1.25, the model will likely predict low sales because it thinks the item is "expensive" relative to that 400 average. In reality, 500 might be the new normal price.

2. relative_yesterday_sales_to_group_mean: we calculate this metric by  `units_sold_yesterday / average_unit_sold_per_sku`. This feature helps model to learn the momentum of the sales_unit of eack sku. If this index is over one then model learn the sales unit will be higher than the average and vice - a versa. As with price index, this relative yesterday sales index is also  highly prone to data leakage. To to avoid we split the data before creating this feature. 

3. relative_moving_averages : we should calculate the relative moving averages of unit sold by diving the `yestererday's unit sold by moving average`. But we should use yersterday's unit sold in calculating moving average. Also, it is important that the yesterday's unit_sold must be properly group by sku.
for example moving average index(weekly) = yesterday's unit sold / df.groupby('sku)['yerterdays unit sold'].transform(lambda x: x.rolling(window=7).mean())`. Having these features is beneficial because they transform raw data into actionable signals that describe the "state" of a product rather than just a number. By using a Sales Index or Relative Moving Average, you provide the model with contextual momentum; it can instantly see if a product is "heating up" (Index > 1) or "cooling down" (Index < 1) relative to its own history. This is much more predictive than raw sales figures because it accounts for the different scales of various products—a sale of 10 units might be a massive spike for a small SKU but a failure for a top-seller. Furthermore, ensuring these are lagged and leak-proof means the model learns stable, real-world relationships between past trends and future outcomes, leading to a forecast that is both statistically accurate and operationally reliable.

4. yesterday_sell_through_rate: we calulate this by dividing yesterday's units sold or each sku / yesterday's stock available for each sku. From EDA we understand that yesterday's sell through rate has some linear relationship with units sold.  It teaches model to think "high stock != high sales but high demand + high stock = high sales.


These are the steps we do.
- Sort the data. Ensure the dataframe is sorted by SKU and Date.
- Create lags/moving averages: use the .groupby('sku') and .shift(1) logic on the full dataset. 
- calculate the group mean (price and unit sold) using only upto the training dates.
- Create a lookup table for the features like moving averages, sell through rate to use in test or validation dataset


#### 4. Feature Engineering, Data Splitting, Model Taining and Evaluations.

In this step, we perform feature engineering, data transformation, model training, and model evaluation.

For `time-series forecasting`, feature engineering requires extra care to `avoid data leakage`. Any feature must be created using `only the information that would have been available at the time of forecasting`. Therefore, `data splitting must be done before feature engineering`, while strictly respecting time continuity.

**steps**:
1. Train-Test Split
    We first split the original dataset into:

    - Train–Validation set (train_val)

    - Test set

    The `test set` is reserved for the final evaluation of the model and must represent the future unseen period.

    The length of the test set depends on the forecast horizon:

    If the forecast horizon is 7 days, <br>
    the test set consists of the last 7 days of the original data.

2. Rolling Train–Validation Splits

    Since we want to evaluate the model across multiple validation windows, we use rolling (walk-forward) validation.

    For each validation:

    - The start of the validation period is the forecast origin

    - The validation set must contain continuous data equal to the forecast horizon

  `Rolling date`: the date from which forecasting begins for a validation fold.

  **Visual representation**

  ```visual Representation

  jan 1        oct1    oct7      oct14      oct21     oct28      nov4
             train1    val1 
                       train2    val2 
                                train3      val3
                                            train4    val4
                                                      train5     val5
  ```

Each validation window (Val 1, Val 2, …) spans 7 consecutive days, and each training set contains all data available before the corresponding rolling date.

Another hurdle is that splitting data after creating the features will can cause the data leakage. For example, if we have average price as feature, which if is a global average price will cause data leakage. Similarly, if we have lag fearture, the forecasting period should only have lag data (in lag_features) till the previous date corresponding to the number of lags. for example of we hare including lag_1 as feature then in the validation set, we can only inlcude the values of features in first day of the forecast origin. This is because, for lag1 feartures second day values for the featrure from from the forecast origing in only available after the first day or use the predicted value value of lag1 in day one of the forecast origin. 

for example:
```example lag data

day    sales  lag1_sales lag2_sales lag3_sales prediction
1      10     -            -         -           -
2      15    10           -          -           -
3      13    15           10         -           -
4      9     13           15         10          -
5      6     9            13         15          -
6      3     6            9          13          -
7      14    3            6          9           -


8      13     14          3          6           10   
9      10     10          14         3           12
10     12     12          10         14          13
```

In this example day 1 to day 7 are the training data and day 8 and day 9 are the validation data. If we create a lag before splitting, see in lag1_sales we have 13 and 10 on 9th adn 10th day. This is data leakage because during forecasting, only the sales before 8th day is available. But those 13 and 10 are from 8th and 9th days sales respectively. 

Step-by-step process

1. Split train_val into multiple training and validation sets using rolling dates.

    - Number of folds = number of rolling dates.

2. Create features only on the training set.

    - Fit scalers and encoders only on training data.

3. Transform validation data using the fitted objects.

    - Use transform, never fit_transform, on validation data.

4. Create features for the validation set carefully:

    - Features for the first validation day use only past observed data.

    - Features for subsequent days are generated using model predictions.

    - This process is known as recursive forecasting.

5. Train the model on each training fold.

    - Predict the validation horizon recursively.

6. Store evaluation metrics for each fold.

    - After all folds, compute the average metric to assess model performance.

7. Final training and testing:

    - Retrain the model on the entire train_val dataset.

    - Evaluate once on the test set, using the same recursive feature creation strategy as in validation.




In [37]:
# Make a copy of aggregated dataframe for feature engineering. Remove unnecessary columns.
df_fe = df_agg_sku.copy()

# Convert the 'date' column to datetime format
df_fe['date'] = pd.to_datetime(df_fe['date'])
df_fe.drop(columns=['brand', 'category', 'segment', 'delivered_qty'], inplace=True) # we dont need this columns as sku is unique identifier for the brand, category, and segment
df_fe.head()

date     sku  stock_available  units_sold  promotion_flag  \
0 2022-01-21  MI-006              985          85        0.250000   
1 2022-01-22  MI-006             1390         119        0.142857   
2 2022-01-22  MI-026              666          48        0.000000   
3 2022-01-23  MI-006             1446         122        0.125000   
4 2022-01-23  MI-026              965          75        0.166667   

   delivery_days  price_unit  
0       2.875000     4.82875  
1       3.428571     5.08000  
2       2.200000     5.38200  
3       3.750000     5.83625  
4       3.000000     4.68500

##### 4.1 Split the dataset into the train_val and test set

Before splitting the dataset, we will create a dummy columns of sku because since `sku` is static column we need to create dummy in whole set.



In [38]:
df_fe = df_fe.copy()

dummies  = pd.get_dummies(df_fe[['sku']], drop_first=True, prefix='sku', dtype=int)

# Concatenate the dummy horizontally back to the original dataframe
df_fe = pd.concat([df_fe, dummies], axis=1)


In [39]:
horizon = 7

date_max = df_fe['date'].max()
test_cuttoff_date = date_max - pd.Timedelta(days=horizon) # test set is lasty 7 days of data
print(f'The cuttoff date for the test set is: {test_cuttoff_date}')



The cuttoff date for the test set is: 2024-12-24 00:00:00


In [ ]:
# Split the test set to keep it untouched
df_train = df_fe[df_fe['date'] <= test_cuttoff_date]
df_train_val = df_train.copy()
df_test = df_fe[df_fe['date'] > test_cuttoff_date]
print(f"""There are {df_test.shape[0]} rows in the test set.\n
The minimum date in the test set is {df_test['date'].min()} and the maximum date is {df_test['date'].max()}.\n
There are {df_test['sku'].nunique()} unique skus in the test set. So for each sku, there are {df_test.shape[0] / df_test['sku'].nunique()} rows in the test set.
""")

# Also save the df_test as csv file to be used later independently as forecasting inputs during inference phase.
forecasting_input = df_test.to_csv(r"../data/sales_forecasting_input.csv", index=False)

There are 210 rows in the test set.

The minimum date in the test set is 2024-12-25 00:00:00 and the maximum date is 2024-12-31 00:00:00.

There are 30 unique skus in the test set. So for each sku, there are 7.0 rows in the test set.



##### Create a copy of df_train_val for data validation

In [41]:
df_train_val_1 = df_train_val.copy()

In [42]:
rolling_dates = hf.calculate_rolling_dates(
    test_cuttoff_date,
    horizon=7,
    n_folds=5
)

print("The rolling dates for the training set in each fold are:")
for date in rolling_dates:
    print(date)

The rolling dates for the training set in each fold are:
2024-11-19 00:00:00
2024-11-26 00:00:00
2024-12-03 00:00:00
2024-12-10 00:00:00
2024-12-17 00:00:00


In [43]:
# Create a custom features
df = hf.create_custom_features(
    df_train_val_1,
    ["sku"],
    "units_sold",
    'date'
)

# Create a temporal features
df = hf.create_temporal_features(
    df,
    "date"
)


In [44]:
# Check if the features are correctly calculated.
df_na = df.isna().sum().reset_index()
df_na = df_na[df_na[0]>0]
print(f"There are {df_na.shape[0]} columns with missing values.")

There are 0 columns with missing values.


Validate if the new features are correctly created. <br>
To validate this, for any timeseries the dates for eack series should be continous and there should not be any gaps. We will therefore test if the eseries has any gaps in dates. 

In [45]:
missing_dates_info = hf.is_date_continous(
    df,
    date_column='date',
    group_columns=['sku']
)


No missing dates found in the time series.


In [46]:
df.describe()

date  stock_available    units_sold  \
count                          23835     23835.000000  23835.000000   
mean   2023-11-07 22:07:34.021397248      1206.334340    153.533501   
min              2022-02-20 00:00:00       279.000000     26.000000   
25%              2023-05-05 00:00:00      1059.500000    117.000000   
50%              2023-11-23 00:00:00      1212.000000    146.000000   
75%              2024-06-09 00:00:00      1360.000000    182.000000   
max              2024-12-24 00:00:00      2055.000000    555.000000   
std                              NaN       222.571183     51.770841   

       promotion_flag  delivery_days    price_unit    sku_MI-002  \
count    23835.000000   23835.000000  23835.000000  23835.000000   
mean         0.149739       3.004049      5.250156      0.026180   
min          0.000000       1.200000      2.345714      0.000000   
25%          0.000000       2.666667      4.714286      0.000000   
50%          0.125000       3.000000      5.248333      0.000000   
75%          0.250000       3.375000      5.787778      0.000000   
max          0.875000       4.800000      8.340000      1.000000   
std          0.130499       0.513712      0.790434      0.159674   

         sku_MI-006    sku_MI-008    sku_MI-011  ...    sku_YO-020  \
count  23835.000000  23835.000000  23835.000000  ...  23835.000000   
mean       0.043591      0.024879      0.025215  ...      0.028278   
min        0.000000      0.000000      0.000000  ...      0.000000   
25%        0.000000      0.000000      0.000000  ...      0.000000   
50%        0.000000      0.000000      0.000000  ...      0.000000   
75%        0.000000      0.000000      0.000000  ...      0.000000   
max        1.000000      1.000000      1.000000  ...      1.000000   
std        0.204188      0.155761      0.156781  ...      0.165769   

         sku_YO-024    sku_YO-029  weekly_ma_units_sold  \
count  23835.000000  23835.000000          23835.000000   
mean       0.025173      0.041997            153.555276   
min        0.000000      0.000000             69.285714   
25%        0.000000      0.000000            124.857143   
50%        0.000000      0.000000            147.000000   
75%        0.000000      0.000000            177.000000   
max        1.000000      1.000000            316.857143   
std        0.156654      0.200587             38.438777   

       monthly_ma_units_sold  sell_through_rate_yesterday   day_of_week  \
count           23835.000000                 23835.000000  23835.000000   
mean              153.628834                     0.127256      2.998280   
min                83.366667                     0.047269      0.000000   
25%               126.100000                     0.101101      1.000000   
50%               147.933333                     0.121380      3.000000   
75%               175.966667                     0.147581      5.000000   
max               274.100000                     0.345364      6.000000   
std                35.541034                     0.035462      2.001415   

       day_of_month  week_of_year         month  
count  23835.000000       23835.0  23835.000000  
mean      15.742522     28.451017      6.958632  
min        1.000000           1.0      1.000000  
25%        8.000000          17.0      4.000000  
50%       16.000000          29.0      7.000000  
75%       23.000000          41.0     10.000000  
max       31.000000          52.0     12.000000  
std        8.764862      14.59378      3.352680  

[8 rows x 42 columns]

##### 4.2 Creating features, trainig model, and recursive forecasting pipeline <br>
Our custom functions to create features work as intended. Now, we write a code to run a workflow to:
1. Split the data into train and validation set for five fold walkthrough validation.
2. Create lag, custom and temporal features for training 
3. Scale numerical features
4. Fit the models 
5. Extract features (lag and custom features (last value of each sku)) from training set to create features for validation set
6. make complete features for validation data 
7. Make a prediction for a day, update the features using the this predicted value and make prediction for next day...repeat this for all horizon.
8. Make seasonal naive model to compare and validate the trained models.




For the first experiment, we will not remove any outliers, see the results without outliers handling. But we will scaled the some fearures (moving average, stock available) as their value and variace are high enough. 

In [47]:
features_to_scale = ['stock_available', "weekly_ma_units_sold", "monthly_ma_units_sold"]

# We will use these custom features from training set to validation set
features_from_training_to_validation = [
    "units_sold_lag_1", 
    "weekly_ma_units_sold", 
    "monthly_ma_units_sold", 
    "sell_through_rate_yesterday"
]

##### Feature engineering, training, recursive predicting pipeline

In [48]:
#-----------Split the dataset into train_val and test set-------------------
final_predictions = []
for origin_date in rolling_dates:
    print(f"Origin date for the fold: {origin_date}")
    training_set = df_train_val[df_train_val['date'] <= origin_date]
    validation_set = df_train_val[(df_train_val['date'] > origin_date) &
                                    (df_train_val['date'] <= origin_date + pd.Timedelta(days=horizon))]
    
    #====================Create a features for the training set========================

    #-------------Create lag features---------------------
    training_data_lags = hf.create_lag_features(
        training_set,
        date_col='date',
        group_column_id=['sku'],
        lag_days=[1],
        target_col='units_sold'
    )
    #-------------Create custome features-------------------
    training_data_fe = hf.create_custom_features(
        training_data_lags,
        group_columns_id=['sku'],
        target_column='units_sold',
        date_column='date'
    )
    #-------------Create temporal features-------------------
    training_data_fe = hf.create_temporal_features(
        training_data_fe,
        date_col="date"
    )
    #================Cretae a history lookup dictionary========================
    history_dict = {
        sku: training_data_fe[training_data_fe['sku'] == sku] for sku in training_data_fe['sku'].unique()
        }
    
    naive_history_dict = {
        sku: df.copy() for sku, df in history_dict.items()
        }   
    # Save the skus and its index for mapping later
    skus = history_dict.keys()
    sku_index_map = {sku: idx for idx, sku in enumerate(skus)}
    
    # ================Scale the features in the training set===================
    scaler = StandardScaler()
    training_data_fe[features_to_scale] = scaler.fit_transform(training_data_fe[features_to_scale])
    print(f"Last date in the training set: {training_data_fe['date'].max()}")

    # --------------Drop the unnecessary columns from the training set and create X_train and y_train-----------------
    X_train = training_data_fe.drop(columns=['date', 'sku', 'units_sold', "price_unit"])
    y_train = training_data_fe['units_sold']

    #=======================Recursive Prediction on the validation set=========================
    validation_set = validation_set.sort_values(by=['sku', 'date']) 
    
    #====================Train the model once and Prepare the validation data, Predict and and Evaluate the model Recursively========

    #-------Initialize the models------------
    models = models

    #----------------------------train the models and store in the models dictionary----------
    prediction_model = []
    for model_name, ModelClass in models.items():
        model = ModelClass()
        fitted_model = model.fit(X_train, y_train)
      
        recursive_history_dict = {
            sku: df.copy() for sku, df in history_dict.items()
        }

        #==========Make a recursive predction for each day in the horizon===========
        predictions_current_day = {}
        for day in range(1, horizon+1):
            current_day = origin_date + pd.Timedelta(days=day)
            val_rows = []
            
            # Make a custom features for the input for the current day using (validation set) and by extracting the
            # last day history from the recursive_history_dict for each sku
            for sku, history_df in recursive_history_dict.items():

                # Create the custom features for validation set for eack sku
                custom_features = hf.make_features_from_history(
                    history_df,
                    date_col='date',
                    features_to_use_in_validation=features_from_training_to_validation
                )
                # Filter the validation set for the current day and sku
                base_features = validation_set[
                    (validation_set['sku'] == sku) & 
                    (validation_set['date'] == current_day)
                    ].copy()
                # Concatenate the base features with the custom features
                validation_row = pd.concat([base_features.reset_index(drop=True), custom_features.reset_index(drop=True)], axis=1)
                val_rows.append(validation_row)
            val_df_current_day = pd.concat(val_rows, axis=0) # vertically stacking all the one row dataframe 

            #--------- Preserve the real `units_sold` value for the current day to evaluate later----------

            actuals = (
                validation_set[validation_set['date'] == current_day]
                .set_index('sku').loc[val_df_current_day['sku'], 'units_sold']
            )
            y_current_day_real = actuals.tolist()
        

            #-----------Create temporal features for the current day validation set------------
            val_df_current_day = hf.create_temporal_features(
                val_df_current_day,
                date_col='date'
            )

            #---------Scale the val_df_current_day's features preserving the unscaled version for updating the recursive history---------
            val_df_current_day_scaled = val_df_current_day.copy()
            val_df_current_day_scaled[features_to_scale] = scaler.transform(val_df_current_day_scaled[features_to_scale])

            #-------------Create X_val and y_val for the current day validation set-------------
            X_val_current_day = val_df_current_day_scaled.drop(columns=['date', 'sku', 'units_sold', "price_unit"])
            X_val_current_day = X_val_current_day.reindex(
                columns=X_train.columns,
                fill_value=0
            )

            #==================== Predict using each trained model and evaluate the predictions ========================
            
            #--------------------Predict current day currrent_model------------------
            y_pred_current_day = fitted_model.predict(X_val_current_day)
            predictions_current_day[current_day.date()] = {

                "actual": y_current_day_real,
                "predicted": y_pred_current_day.tolist()
            }   
            # Update the recursive history _dict with the predicted values for the current day
            for i, sku in enumerate(val_df_current_day['sku']):
                new_row = val_df_current_day.iloc[[i]].copy()
                new_row['units_sold'] = y_pred_current_day[i]
                recursive_history_dict[sku] = pd.concat([recursive_history_dict[sku], new_row], axis=0)

        prediction_model.append({
            "origin_date": origin_date,
            "model_name": model_name,
            "predictions": predictions_current_day
        })

    #=========================Naive seasonal Prediction===================================
    naive_prediction_current_day = {}
    for day in range(1, horizon+1):
        current_day = origin_date + pd.Timedelta(days=day)
        target_date = current_day  - pd.Timedelta(days=horizon)

        naive_predictions_current_day = []
        y_current_day_real = []
        for sku, history_df in naive_history_dict.items():
    
            mask  = (
                (validation_set['sku'] == sku) &
                (validation_set['date'] == current_day)
            )
            real_val = validation_set.loc[mask, 'units_sold']
            if real_val.empty:
                continue
            y_current_day_real_val = real_val.iloc[0]
            y_current_day_real.append(y_current_day_real_val)
            naive_val = history_df.loc[history_df['date'] == target_date, 'units_sold']
            naive_val = naive_val.iloc[0] if len(naive_val) > 0 else np.nan
            naive_predictions_current_day.append(naive_val)
        naive_prediction_current_day[current_day.date()] = {
            "actual": y_current_day_real,
            "predicted": naive_predictions_current_day   
        }
    prediction_model.append({
        "origin_date": origin_date,
        "model_name": "naive_seasonal",
        "predictions": naive_prediction_current_day
    })

    final_predictions.append(prediction_model)
print("Prediction on the validation set is completed.")




Origin date for the fold: 2024-11-19 00:00:00
Last date in the training set: 2024-11-19 00:00:00
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000204 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1558
[LightGBM] [Info] Number of data points in the train set: 22785, number of used features: 40
[LightGBM] [Info] Start training from score 154.910819
Origin date for the fold: 2024-11-26 00:00:00
Last date in the training set: 2024-11-26 00:00:00
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000170 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1558
[LightGBM] [Info] Number of data points in the train set: 22995, number of used features: 40
[LightGBM] [Info] Start training from score 1

##### 4.3 Evaluation of forecast results of walkforward validations

##### *MAE and R2 of each model for each horizon day*

In [49]:
rows = []
for results in final_predictions:
    for result in results:
        origin_date = result['origin_date']
        model_name = result['model_name']


        for forecast_day, predictions in result['predictions'].items():
            y_true = predictions['actual']
            y_pred = predictions['predicted']
            mae = round(mean_absolute_error(y_true, y_pred), 1)
            r2 = round(r2_score(y_true, y_pred), 1)

            horizon_day = (forecast_day - origin_date.date()).days
            rows.append({
                "origin_date": origin_date,
                "model_name": model_name,
                "forecast_day": forecast_day,
                "horizon_day": horizon_day,
                "mae": mae,
                "r2": r2
            })

                              
results_df = pd.DataFrame(rows)
results_df.sort_values(by=['origin_date', 'horizon_day', "mae"], ascending=True, inplace=True) 
result_df_agg_model_horizon = results_df.groupby(['model_name', 'horizon_day']).agg({
    "mae": "mean",
    "r2": "mean"
}).reset_index()

result_df_agg_model_horizon.sort_values(by=["horizon_day", "mae"], ascending=True, inplace=True)


In [50]:
fig = px.bar(
        result_df_agg_model_horizon,
        x="horizon_day",
        y="mae",
        # facet_col="model_name",
        color= "model_name",
        barmode='group',
        title="Mean Absolute Error by Model and Horizon Day",
        color_discrete_sequence=px.colors.sequential.ice
        
)
fig.show()

In [51]:
fig = px.bar(
        result_df_agg_model_horizon,
        x="horizon_day",
        y="r2",
        # facet_col="model_name",
        color= "model_name",
        barmode='group',
        title="R-squared by Model and Horizon Day",
        color_discrete_sequence=px.colors.sequential.ice
        
)
fig.show()

All the models have learned important patterns in the data. This is clearly visible from the large difference in MAE between the seasonal naive model and the machine learning models. The naive model performs much worse, which confirms that the ML models are capturing meaningful relationships rather than relying only on seasonality.

Most of the tree-based ensemble models show consistently good MAE across all forecast horizons. For the given SKUs, where units sold typically range between 30 and 300, an MAE between 9 and 12 units is considered very good. Even the linear regression model performs reasonably well, with an MAE of around 14 units. This indicates that the engineered features are informative and useful for forecasting units_sold.

Among all models, Extra Trees and Histogram Gradient Boosting consistently perform the best across all horizon days, showing both stability and accuracy.

Looking at the R² scores, most ensemble models and the linear regression model achieve values above 0.8, which means a large portion of the variation in units_sold is explained by the model features. Considering this is a global model forecasting sales for around 30 SKUs, an R² above 0.8 can be considered very strong performance.

It is also worth noting that the Decision Tree model performs worse than the ensemble models and is the weakest model after the naive baseline. Although its metric scores are not extremely poor, the decision tree does not generalize well, which is a common limitation of single-tree models compared to ensemble approaches.

##### 4.3.1 Summarization of MAE and R Squared

*Summarize the MAE and R2 of each model*






In [52]:

rows = []
for results in  final_predictions:
    for result in results:
        origin_date = result['origin_date']
        model_name = result['model_name']
        for forecast_day, forecast_values in result['predictions'].items():
            actuals = forecast_values['actual']
            predictions = forecast_values['predicted']

            for i in range(len(actuals)):
                rows.append({
                    "origin_date": origin_date,
                    "model_name": model_name,
                    "forecast_day": forecast_day,
                    "sku_index": i,
                    "actual": actuals[i],
                    "predicted": predictions[i]
                })

# Create a DataFrame from the rows
results_df = pd.DataFrame(rows)

In [53]:
result_dfs = results_df.sort_values(by=['sku_index', "forecast_day"])
results_df_pivot = results_df.pivot_table(
    index=['forecast_day', "sku_index"],
    columns="model_name",
    values=['actual', 'predicted']
)

results_df_pivot.columns = [f"{model}_{value}" for value, model in results_df_pivot.columns]
results_df_pivot = results_df_pivot.reset_index()
results_df_pivot.drop(columns=[col for col in results_df_pivot.columns if '_actual' in col and col != 'naive_seasonal_actual'], inplace=True)
# Calculate MAR and RMSE for each model
predicted_columns = [str(col.split("_predicted")[0]) for col in results_df_pivot.columns if '_predicted' in col]
score = {}
for col in predicted_columns:
        score[f"mae_{col}"] = mean_absolute_error(results_df_pivot['naive_seasonal_actual'], results_df_pivot[f'{col}_predicted'])
        score[f"r2_{col}"] = r2_score(results_df_pivot['naive_seasonal_actual'], results_df_pivot[f'{col}_predicted'])

# Convert the score dictionary into nice looking pandas table 
rows = []
for key, value in score.items():
        model_name = key.split("_")[1]
        metric = key.split("_")[0]
        rows.append({
                "Model": model_name.upper(),
                metric.upper(): value
        })
df = pd.DataFrame(rows)

df_final = df.pivot_table(index="Model", values=['MAE', 'R2']).reset_index()
    
df_final.sort_values(by=["MAE", "R2"], ascending=[True, False], inplace=True)

df_final



Model        MAE        R2
3   LGBM  10.711041  0.860606
2    HGB  10.736651  0.860380
1     ET  10.743381  0.856291
7    XGB  10.829325  0.860278
6     RF  11.094524  0.849110
4     LR  13.059720  0.805162
0     DT  15.609524  0.686154
5  NAIVE  34.661905 -0.370666

In an agrregate, HGB is a winner as it resulted in best `MAE` of 10.70 and  `R2` of 0.86. 
Lets plot the residuals in hitogram to see the distribution of errors.

*Diognosis of HGB model*

In [54]:
# Plot the residual errors for the best model 
results_df_pivot['residuals_best_model'] = results_df_pivot['naive_seasonal_actual'] - results_df_pivot['lgbm_predicted']

In [55]:
residual_histogram = px.histogram(
    results_df_pivot, 
    x='residuals_best_model',
    title="Residuals Distribution for the Best Model (LGBM)").update_layout(width=500, height=300)

residual_histogram.show()

The histogram of residuals for the best model (LGBM) looks close to a normal (bell-shaped) distribution. Most of the errors are centered around 0, which means the model does not consistently over-predict or under-predict.

Around 97% of the residuals fall between −22 and +22, showing that most prediction errors are relatively small. This indicates that the model is making accurate and stable predictions for most cases.

The distribution is slightly right-skewed, with a few large positive errors above 50. These extreme values may be caused by unusual demand spikes, noise in the data, or events that the model could not fully capture.

Overall, the residual pattern suggests that the model fits the data well and that most of the remaining errors are random rather than systematic, which is a good sign for a forecasting model.

##### 4.3.2 Visualize the Predicted value of the best model in line chart


We will visualize the predictions of  `units_sold` by a `LGBM` (best model), in a line chart, so that we can compare how the predictions differ 
from the actuals. To to that we need to do:
1. Prepare a dataframe that contains the actual and predicted values of each model, per sku and per forecast_day.
2. Pivot the dataframe from to make it wide as per the model predicted value
3. Fill the dates to the pivoted dataframe. In the pivot dataframe each sku should have matching date range from the oroginal dataframe (df_train_val)
4. Finally, merge the pivoted dataframe to the original dataframe. 
5. visualize the actuals and predicted valies in a line chart





*1. Prepare datafame to include the actual and predicted values of eact model, per sku and per forecast_day.* 
We have already preared the dataframe call `results_df` in 4.3.1.

*2. Pivot the dataframe to make it wide*
We have also pivoted the dataframe `result_df_pivot` in 4.3.1, which is reshaped into wide format from long format. 





*3. Fill the dates to the pivoted dataframe*

In [56]:
# Calculate the date range from the df_train_val for each sku in the results_df_pivot

date_range_dict = {}
for sku in df_train_val['sku'].unique():
    # filter the dataframe by sku
    df_train_val_sku = df_train_val[df_train_val['sku'] == sku]
    # Store the min and max date in the dictionary
    date_range_dict[sku] = {
        "min_date": df_train_val_sku['date'].min(),
        "max_date": df_train_val_sku['date'].max()
    }

# Map the sku_index to sku in results_df_pivot
results_df_pivot['sku'] = results_df_pivot['sku_index'].map({index: sku for sku, index in sku_index_map.items()})

results_df_pivot['forecast_day'] = pd.to_datetime(results_df_pivot['forecast_day'])

full_dates_df_sku = pd.DataFrame()
for sku in results_df_pivot['sku'].unique():
    min_date = date_range_dict[sku]['min_date'] 
    max_date = date_range_dict[sku]['max_date']
    date_range = pd.date_range(start=min_date, end=max_date, freq='D')
    sku_date = pd.DataFrame({
        "date": date_range,
        "sku": sku
    })
    full_dates_df_sku = pd.concat(
        [full_dates_df_sku, sku_date],
        axis=0
    )
    
# Merge the full_dates_df_sku with the results_df_pivot to the get the full date range for each sku
full_dates_df_sku_pivot = full_dates_df_sku.merge(
    results_df_pivot,
    left_on=['date', 'sku'],
    right_on=['forecast_day', 'sku'],
    how='left'
)

# 

*4. Merge the pivot datarame, containing full date range, with the df_train_val*

In [57]:
original_df = df_train_val[['date', 'sku', 'units_sold']].copy()
merged_full_df = original_df.merge(
    full_dates_df_sku_pivot,
    on=['date', 'sku'],
    how='left'
)


In [58]:
random_sku = random.choice(list(merged_full_df['sku'].unique()))

fig = px.line(
    merged_full_df[merged_full_df['sku'] == random_sku],
    x='date',
    y=['units_sold', 'lgbm_predicted', 'naive_seasonal_predicted'],
    title=f"Actual vs Predicted Units Sold for SKU: {random_sku}, Model-LGBM vs Naive Seasonal",
    line_dash='variable',
    color_discrete_map ={
        'units_sold': 'blue',
        'hgb_predicted': 'red',
        'naive_seasonal_predicted': 'lightgrey'
    }
)

fig.update_layout(yaxis_title="Units Sold", width=1000, height=500)
fig.show()



#### 5. Train a LGBM model with full `training set` and evaluate on test set
From the 5 fold walkthrough validations, we found that all treebased ensemble model performed well. LightGBM was the top performer though. So we will train the `lightgbm` on full training set and evaluated on test set. 

In [59]:
from lightgbm import LGBMRegressor

In [60]:
#======================Create features on test set====================================

#----------Create lag features on the training set-------------------
df_train = hf.create_lag_features(
    df_train,
    date_col='date',
    lag_days=[1],
    target_col="units_sold",
    group_column_id=['sku']
)
#----------Create custom features on the training set-------------------
df_train = hf.create_custom_features(
    df_train,
    group_columns_id=['sku'],
    target_column='units_sold',
    date_column='date'
)
#----------Create temporal features on the training set------------------
df_train = hf.create_temporal_features(
    df_train,
    date_col='date'
)
# Create a copy of df_train for scaling and but keepig df_train unscaled for updating history during prediction
df_train_scaled = df_train.copy()

#----------Scale the features in the trainig set -------------------
scaler = StandardScaler()   
df_train_scaled[features_to_scale] = scaler.fit_transform(df_train_scaled[features_to_scale])


#=====================Train the HGM Model of the trainig set=======================

# -------------Create X_train and y_train----------------\
X_train = df_train_scaled.drop(columns=['date', 'sku', 'units_sold', 'price_unit'])
y_train = df_train_scaled['units_sold']

lgbm =  LGBMRegressor(
    random_state=42,
    max_iter=200,
)
fitted_lgbm = lgbm.fit(X_train, y_train)

#=====================Prepare the test set and make predictions recursively=======================

# Create a history lookup dictionary
history_dict = {
    sku: df_train[df_train['sku'] == sku] for sku in df_train['sku'].unique()
}

predictions_test = {}
df_test= df_test.sort_values(by=['sku', 'date']) 
for day in range(1, horizon+1):
    current_day = test_cuttoff_date + pd.Timedelta(days=day)
    test_set = df_test[df_test['date'] == current_day].sort_values(by=['sku', 'date'])
    
    test_rows_current_day = []
    actuals_current_day = []
    for sku in test_set['sku'].unique():
        # Get the base row from the test set for the current sku
        base_row = test_set[test_set['sku'] == sku]
        
        custom_features = hf.make_features_from_history(
            history_dict[sku],
            date_col="date",
            features_to_use_in_validation=features_from_training_to_validation
        )
        # concatenate the base row with the custom features 
        test_row_current_day = pd.concat([base_row.reset_index(drop=True), custom_features.reset_index(drop=True)], axis=1)
        test_rows_current_day.append(test_row_current_day)
    test_df_current_day = pd.concat(test_rows_current_day, axis=0)

    #-----------Create temporal fetures for the test df current day------------
    test_df_current_day = hf.create_temporal_features(
        test_df_current_day,
        date_col='date'
    )
    #-------------------Preserve the actuals for the current day test set to evaluate later-------
    actuals = test_set.set_index('sku').loc[test_df_current_day['sku'], 'units_sold']
    actuals_current_day = actuals.tolist()

    #--------Scale the test df current day features preserving the unscaled version for udating the history dict--------
    test_df_current_day_scaled = test_df_current_day.copy()
    test_df_current_day_scaled[features_to_scale] = scaler.transform(test_df_current_day_scaled[features_to_scale])

    #-------------Create X_test for the current day test set------------
    X_test_current_day = test_df_current_day_scaled.drop(columns=['date', 'sku', 'units_sold', "price_unit"])
    X_test_current_day = X_test_current_day.reindex(
        columns=X_train.columns,
        fill_value=0
    ) 
    # ----------------Predict using the trained LGBM model----------------
    y_test_pred_current_day = fitted_lgbm.predict(X_test_current_day)

    # Save the predictions and actual for the current day
    predictions_test[day] = {
        "actual": actuals_current_day,
        "predicted": y_test_pred_current_day.tolist()
    }
    #----------update the history_dict with the predicted values for the current day
    for i, sku in enumerate(test_df_current_day['sku']):
        new_row = test_df_current_day.iloc[[i]].copy()
        new_row['units_sold'] = y_test_pred_current_day[i]
        history_dict[sku] = pd.concat([history_dict[sku], new_row], axis=0)

print("Model Training on full training set and Prediction on the test set is completed.")


[LightGBM] [Warning] num_iterations is set=200, max_iter=200 will be ignored. Current value: num_iterations=200
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000666 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1558
[LightGBM] [Info] Number of data points in the train set: 23835, number of used features: 40
[LightGBM] [Info] Start training from score 153.533501
Model Training on full training set and Prediction on the test set is completed.


##### 5.1 Evaluation of `LGBM` on test set

In [61]:

rows = []
for day, results in predictions_test.items():
    actuals = results['actual']
    predictions = results['predicted']
    for i, (actual, predicted) in enumerate(zip(actuals, predictions)):
        rows.append({
            'day': day,
            'actual': actual,
            'predicted': predicted,
            'sku_index': i
        })
result_df = pd.DataFrame(rows)

In [62]:
# Calculation of MAE and R2 for each horizon day
metrics_per_horizon = []
for horizon in result_df['day'].unique():
    df_horizon = result_df[result_df['day'] == horizon]
    mae = mean_absolute_error(df_horizon['actual'], df_horizon['predicted'])
    r2 = r2_score(df_horizon['actual'], df_horizon['predicted'])
    metrics_per_horizon.append({
        'horizon_day': horizon,
        'mae': mae,
        'r2': r2
    })
metrics_df = pd.DataFrame(metrics_per_horizon)
print("Test Set Evaluation Metrics by horizon day:\n")
print(metrics_df.set_index("horizon_day"))



Test Set Evaluation Metrics by horizon day:

                   mae        r2
horizon_day                     
1             8.467323  0.904128
2             9.947337  0.826262
3             8.870010  0.922277
4            10.727109  0.859751
5            10.952638  0.760940
6            10.471119  0.846634
7            11.831420  0.876655


In [63]:
overall_metrics = {
    "mae": mean_absolute_error(result_df['actual'], result_df['predicted']),
    "r2": r2_score(result_df['actual'], result_df['predicted'])
}
print("Overall Test Set Metrics:\n")
print(f"MAE: {overall_metrics['mae']:.3f}")
print(f"R2: {overall_metrics['r2']:.3f}")

Overall Test Set Metrics:

MAE: 10.181
R2: 0.869


In [64]:
# Plot the residuals histograms for the test set predictions 
result_df['residuals'] = result_df['actual'] - result_df['predicted']
fig_residuals_hist = px.histogram(
    result_df,
    x='residuals',
    nbins=40,
    title="Residuals Distribution for the Test Set Predictions"
).update_layout(width=500, height=300)
fig_residuals_hist.show()

The distribution of residuals shows a normally distributed pattern, where about 90 percent residuals ranges from -12 to 12. There are only few instances where residuals is just over +- 30. This is very good result as the most of actual unitsold ranges from 30 to 300 and in some cases 450 to 500 units sold. This shows model is resonably accurate in predicting the units sold for 7 horizon days. 

##### 5.3 Compare the actuals vs predicted in a linechart.

To create a line chart to show the continous dates of train and test and plot the line chart, we need to merge the 'result_df` with the original df. These are the steps needed to merge dfs and visualize:
1. create a data using the `day` column and `test_cutt_off_date
2. create  'sku' columns using the sku_index in result_df and the asku_index_map' dictionary created earlier
3. Create data range for each sku based on original_df (before datasplit) and merge it with the the result_df
4. Merge the result df with the df_train
5. Visualize line chart

In [65]:
# Create a date using 'day' column in the result_df
print(f"The test cuttoff date is: {test_cuttoff_date}")
result_df['forecast_date'] = test_cuttoff_date + pd.to_timedelta(result_df['day'], unit='D')
result_df['forecast_date'] = pd.to_datetime(result_df['forecast_date'])

# Map the sku_index to sku in result_df 
result_df['sku'] = result_df['sku_index'].map({index: sku for sku, index in sku_index_map.items()})

# Create a full date range for each sku in the result_df 
date_range_dict = {}
for sku in df_test['sku'].unique():
    # filter the original dataframe by sku 
    df_agg_sku = df_agg_sku_metrics_merged[df_agg_sku_metrics_merged['sku'] == sku]
    date_range_dict[sku] = {
        "min_date": df_agg_sku['date'].min(),
        "max_date": df_agg_sku['date'].max()
    }
full_dates_df_sku = pd.DataFrame()
for sku in result_df['sku'].unique():
    min_date = date_range_dict[sku]['min_date'] 
    max_date = date_range_dict[sku]['max_date']
    date_range = pd.date_range(start=min_date, end=max_date, freq='D')
    sku_date = pd.DataFrame({
        "date": date_range,
        "sku": sku
    })
    full_dates_df_sku = pd.concat(
        [full_dates_df_sku, sku_date],
        axis=0
    )
# Merge the full_dates_df_sku with the results_df_pivot to the get the full date range for each sku
full_dates_df_sku = full_dates_df_sku.merge(
    result_df,
    left_on=['date', 'sku'],
    right_on=['forecast_date', 'sku'],
    how='left'
)



The test cuttoff date is: 2024-12-24 00:00:00


In [66]:
# Merge the full_dates_df_sku with the original df_train to get the actual units_sold values
original_df = df_agg_sku_metrics_merged[['date', 'sku', 'units_sold']].copy()
original_df['date'] = pd.to_datetime(original_df['date'])
merged_full_df_sku = original_df.merge(
    full_dates_df_sku,
    on=['date', 'sku'],
    how='left'
)

In [67]:
random_sku = random.choice(list(merged_full_df_sku['sku'].unique()))

px.line(   
    merged_full_df_sku[merged_full_df_sku['sku'] == random_sku],
    x='date',
    y=['units_sold', 'predicted'],
    title=f"Actual Sales vs Predicted `units_sold` for SKU: {random_sku}"
).show()

#### 6. Save the final model as pickle file

In [69]:
import pickle

feature_config = {
    "lag_days": [1],
    "custom_features": features_from_training_to_validation,
    "target_col": "units_sold",
    "date_col": "date",
    "group_col_id": ["sku"],
    "features_to_scale": features_to_scale
}

# Save last 7 days of training data for each sku to be used for creating features during inference
last_7_days_history = df_train.sort_values(by=['sku', 'date']).groupby('sku').tail(7)

artifacts = {
    "model": fitted_lgbm,
    "scaler": scaler,
    "feature_columns": X_train.columns.tolist(),
    "feature_config": feature_config,
    "history_df": last_7_days_history,
    'functions': {
        'create_temporal_features': hf.create_temporal_features,
        'make_features_from_history': hf.make_features_from_history
    },
    "sku_index_map": sku_index_map
}

with open(r'../models/lgbm_model.pkl', 'wb') as f:
    pickle.dump(artifacts, f)

#### 7. Serving model for forecasting `units_sold` for 7 days <br>
For serving the model, we need following:
1. trained model
2. scaler
3. feature_columns
4. historical features values (alteast the features used in last origin date as the custom features of this date will be used to make the first prediction)
5. Other artifacts like date column, group_id column ot any other artifacts needed to prepare the data for the predictions. 

We have saved all the necessary above materials as artifacts while saving the pickle file. We will load those artifacts and use it for the forecast.

##### 7.1 Load the artifacts

In [70]:
import pickle
import pandas as pd
with open(r'../models/lgbm_model.pkl', 'rb') as f:
    loaded_artifacts = pickle.load(f)
print(f"loaded artifacts keys: {loaded_artifacts.keys()}")
print(f"model: {loaded_artifacts['model']}")

loaded artifacts keys: dict_keys(['model', 'scaler', 'feature_columns', 'feature_config', 'history_df', 'functions', 'sku_index_map'])
model: LGBMRegressor(max_iter=200, random_state=42)


##### 7.2 Prepare the necessary data for inference—create features for the new data points

In [71]:
# =========Forcasting data ============
"""for the simulation purpose, we will use the test set as the new data to forecast the next 7 days after the test set date range.
In real scenario, this new data will be the new incoming data for which we have to forecast
"""
forecasting_inputs = pd.read_csv('sales_forecasting_input.csv')
forecasting_inputs['date'] = pd.to_datetime(forecasting_inputs['date'])

forecasting_inputs.drop(columns=['units_sold'], inplace=True)

# Define the origin date and horizon for forecasting
origin_date = test_cuttoff_date # The date from which the forecast will start
horizon = horizon # the horizon is 7 days

# ==========Extract the data from the artifacts===========
last_7_days_history = loaded_artifacts['history_df']
custom_features = loaded_artifacts['feature_config']['custom_features']
date_col = loaded_artifacts['feature_config']['date_col']
features_to_scale = loaded_artifacts['feature_config']['features_to_scale']
scaler = loaded_artifacts['scaler']
model = loaded_artifacts['model']
feature_columns = loaded_artifacts['feature_columns']
sku_index_map = loaded_artifacts['sku_index_map']

# ===========functions===========
create_temporal_features = loaded_artifacts['functions']['create_temporal_features']
make_features_from_history = loaded_artifacts['functions']['make_features_from_history']



##### 7.3 Inference Pipeline

In [72]:
# # ==========Make recursive forecasts for the horizon period===========

# Look up dataframe for each sku history and add the new rows from the forecasting recursively
history_dict = {
    sku: last_7_days_history[last_7_days_history['sku'] == sku] for sku in last_7_days_history['sku'].unique()
}
# 
forecasts_horizon = {} # to store the forecasts for each day in the horizon
for day in range(1, horizon+1):
# 
    # Prepare the features for the forecasting recursively using base features and history_dict.
    current_day = origin_date + pd.Timedelta(days=day)
    inputs_current_day = forecasting_inputs[forecasting_inputs['date'] == current_day].copy()
    inputs_current_day.sort_values(by=['sku', 'date'], inplace=True)
    # print(inputs_current_day)
    # 
    rows_current_day = []
    for sku in inputs_current_day['sku'].unique():
        # Get the base row from the inputs for the current sku
        base_row = inputs_current_day[inputs_current_day['sku'] == sku]
        custom_features = make_features_from_history(
            history_dict[sku],
            date_col=date_col,
            features_to_use_in_validation=custom_features
        )
        current_day_row = pd.concat([base_row.reset_index(drop=True), custom_features.reset_index(drop=True)], axis=1)
        rows_current_day.append(current_day_row)
    inputs_current_day_df = pd.concat(rows_current_day, axis=0)
    inputs_current_day_df = create_temporal_features(
        inputs_current_day_df,
        date_col=date_col
    )
    inputs_current_day_df_scaled = inputs_current_day_df.copy()
    inputs_current_day_df_scaled[features_to_scale] = scaler.transform(
        inputs_current_day_df_scaled[features_to_scale]
    )
    # drop the unnecessary columns
    inputs_current_day_df_scaled.drop(
        columns=['date', 'sku', 'price_unit'], 
        inplace=True)
    inputs_current_day_df_scaled = inputs_current_day_df_scaled.reindex(
        columns=feature_columns,
        fill_value=0)
    
    # make predictions
    forecasts = model.predict(inputs_current_day_df_scaled)
    forecasts = forecasts.tolist()
    forecasts_horizon[current_day.date()] = [int(forecast) for forecast in forecasts] # Converting to the neareast integer

    # Update the history_dict with the predicted values for the current day
    for i, sku in enumerate(inputs_current_day_df['sku']):
        new_row = inputs_current_day_df.iloc[[i]].copy()
        new_row['units_sold'] = forecasts[i]
        history_dict[sku] = pd.concat([history_dict[sku], new_row], axis=0)

    # 
print("Forecasting for the horizon period is completed.")
print("#","="*100,"#\n")
print("Forecasted values for each day in the horizon:")
forecasts_horizon = pd.DataFrame(forecasts_horizon)
# forecasts_horizon
forecasts_horizon['sku'] = forecasts_horizon.index.map({index: sku for sku, index in sku_index_map.items()})
forecasts_horizon.set_index("sku", inplace=True)
forecasts_horizon

Forecasting for the horizon period is completed.
# ==================================================================================================== #

Forecasted values for each day in the horizon:


2024-12-25  2024-12-26  2024-12-27  2024-12-28  2024-12-29  \
sku                                                                  
JU-021          42          79         103         117         121   
MI-002         166         156         130         116         181   
MI-006          99          95         111          82         118   
MI-008          67         124         101          73          87   
MI-011         105          85         104          73          84   
MI-022         128          62          89          80          99   
MI-023         148         109         171         164         144   
MI-026          69         113          64         149         194   
RE-004         208         117         150         161         132   
RE-007         137         143         184         105         224   
RE-015         176         190         123         197         142   
RE-017         126         180         220         143         110   
RE-025         113          96         124         130         161   
SN-010         137         125         108         134         133   
SN-013          78         118          96         104         131   
SN-019         101         152         105         118         140   
SN-027          70          97          97         105         100   
SN-028         148         162         182         122         100   
SN-030         123         104         150         105         120   
YO-001         114         109         123         119         117   
YO-003         111         128         140          91         118   
YO-005          92         136         106         129         143   
YO-009         106         147         111         102         129   
YO-012         135         110          88         143         102   
YO-014          99          91          99          65          97   
YO-016         102         125         136         116         158   
YO-018         113          95         115         134         140   
YO-020         118          92         146         160          83   
YO-024          95         138         101         105         127   
YO-029         117         129         149          83         128   

        2024-12-30  2024-12-31  
sku                             
JU-021          73         110  
MI-002         135          97  
MI-006         107          77  
MI-008         106          95  
MI-011         102          93  
MI-022         114          74  
MI-023         109         126  
MI-026         135          73  
RE-004         151         152  
RE-007         187         235  
RE-015         122         197  
RE-017         216         108  
RE-025         209         104  
SN-010         157          75  
SN-013          84          63  
SN-019         167         108  
SN-027          76          90  
SN-028         144          98  
SN-030         108         150  
YO-001         120          94  
YO-003         167          91  
YO-005         113         154  
YO-009         130         152  
YO-012         124         118  
YO-014          70         103  
YO-016         124         165  
YO-018         125         119  
YO-020         107         174  
YO-024         164         144  
YO-029         122         115

#### 8. Conclusion
In this project, we successfully developed a `machine learning–based global forecasting model` to predict 7-day ahead sales units for multiple SKUs. The model uses a *recursive forecasting strategy*, where predictions from earlier horizon days are used as inputs for later days. Although recursive forecasting can propagate errors across the forecast horizon, the model achieved strong and stable performance, indicating that error accumulation is well controlled.

To ensure the reliability of the results, special care was taken to avoid *data leakage*. All features were generated strictly using historical information available up to each prediction date, and the same feature generation logic was consistently applied during training, validation, and testing. The feature set includes lag-based, rolling, and temporal features, which were carefully designed to capture sales trends, seasonality, and short-term dynamics.

We conducted a *5-fold walk-forward (rolling) validation*, which closely resembles real-world forecasting conditions. The validation results showed consistent performance across folds, confirming that the model generalizes well over time. From these experiments, we concluded that the engineered features are highly informative and successfully capture important patterns in the data.

Across all experiments, tree-based ensemble models performed particularly well, achieving `R²` scores above `0.85` and `MAE` values around `9` units. Considering that most SKUs have daily sales ranging from `30 to 300 units`, and occasionally reaching `450–500 units`, this level of error is considered very good. Additionally, the model was trained as a global model across `30 different time series (SKUs)`, which further highlights its robustness and ability to learn shared patterns across products.

Based on both validation and test set performance, `LightGBM` was selected as the final model. This choice was made not only due to its strong predictive accuracy, but also because of its efficient and lightweight architecture, which is suitable for large-scale and production use. The final model was trained on the full training dataset and evaluated on a hold-out test set, where it achieved results consistent with validation performance. This confirms that the model is stable and reliable.

Finally, the trained model and all required `artifacts—including the scaler, feature column definitions, feature engineering functions, and the last available historical data`—were saved and reused to generate `batch forecasts`. This ensures that the inference pipeline is reproducible and aligned with the training process.

Future Work

Several enhancements can be explored to further improve the forecasting system:

Direct multi-step forecasting
Instead of recursive forecasting, separate models can be trained for each forecast horizon to reduce error propagation.


SKU-level diagnostics
Analyze performance per SKU to identify products that may benefit from specialized models.

Online or incremental learning
Periodically retraining or updating the model with new data could help adapt to changing demand patterns.

Production deployment
The model can be deployed as a scheduled batch job or an API service for real-time inference.






